<h1>A Copy of Hannah's Notebook for Support Vector Regression</h1>

In [50]:
import numpy as np
import pandas as pd
import random
import matplotlib.pyplot as plt
from scipy.stats import norm
from sklearn.svm import SVR
import math
from evaluator import pinball_loss

General functions from Jake

In [51]:
# We import the sample_submission.csv file as a way of determining
# the order of the rows in out output file
sample_submission = pd.read_csv("../sample_submission.csv")
daily_deaths = pd.read_csv("../data/us/covid/nyt_us_counties_daily.csv")
cumulative_deaths = pd.read_csv("../data/us/covid/deaths.csv")

# Relevant dates
today = cumulative_deaths.columns[-1]
yesterday = cumulative_deaths.columns[-2]
one_week_ago = cumulative_deaths.columns[-8]
two_weeks_ago = cumulative_deaths.columns[-15]
beginning = cumulative_deaths.columns[4]

print("Today: " + today)
print("One week ago: " + one_week_ago)

# Assume date is in format mm/dd/yy, convert to yyyy-mm-dd
def convert_date_to_yyyy_mm_dd(date):
    parts = date.split('/')
    
    # Ensure leading zeros if necessary
    if len(parts[0]) == 1:
        parts[0] = "0" + parts[0]
    
    if len(parts[1]) == 1:
        parts[1] = "0" + parts[1]
        
    return "2020" + "-" + parts[0] + "-" + parts[1]

# Assume date is in format yyyy-mm-dd, convert to mm/dd/yy
def convert_date_to_mm_dd_yy(date):
    parts = date.split('-')
    
    # Remove leading zeros if necessary
    if parts[1][0] == "0":
        parts[1] = parts[1][1:]
    
    if parts[2][0] == "0":
        parts[2] = parts[2][1:]
        
    return parts[1] + "/" + parts[2] + "/" + "20"

# Get the name of a county from a given FIPS code
def get_name_from_fips(FIPS):
    return key.loc[key["FIPS"] == FIPS]["COUNTY"].values[0]

# Get the date of the first death of a given county. If the
# county has no deaths, return "N/A"
def get_date_of_first_death(FIPS):
    county = cumulative_deaths.loc[cumulative_deaths["countyFIPS"] == FIPS]
    deaths_dates = county.drop(columns=['countyFIPS', 'County Name', 'State', 'stateFIPS'])
    lst = deaths_dates.values[0]

    for i in range(len(lst)):
        if lst[i] != 0:
            return deaths_dates.columns[i]

    return "N/A"

# Returns true if there exists deaths data for the county,
# and false otherwise. We need this because some FIPS are
# not included in the ny times data at all.
def deaths_data_exists(FIPS):
    return len(daily_deaths.loc[daily_deaths["fips"] == FIPS].values) != 0

# Generate the quantiles for a given value and standard error
# according to a normal distribution.
def generate_quantiles(value, err):
    if err == 0:
        return [value] * 9
    
    quantiles = []
    for quantile in [0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9]:
        quantiles.append(norm.ppf(quantile, loc=value, scale=err))

    return quantiles

# Generate quantiles for a given list of values and errors
def generate_list_quantiles(lst, err_lst):
    quantiles = []
    for i in range(len(lst)):
        quantiles.append(generate_quantiles(lst[i], err_lst[i]))

    return quantiles

def get_id_list():
    return sample_submission["id"].values

def extract_date_from_id(row_id):
    split = row_id.split('-')
    return '-'.join(split[:-1])

def extract_fips_from_id(row_id):
    return row_id.split('-')[-1]

# Get all dates used over the course of the term
all_dates = sample_submission["id"].values.copy()

for i in range(len(all_dates)):
    all_dates[i] = extract_date_from_id(all_dates[i])

# Remove duplicates in the list
all_dates = list(dict.fromkeys(all_dates))

# Given a start date and an end date in yyyy/mm/dd format,
# return a list of the dates within that range that includes
# both endpoints
def get_dates_in_range(startDate, endDate):
    dates = all_dates[all_dates.index(startDate):all_dates.index(endDate) + 1]
    return dates

# Starting from a given date, take an input number of steps
# and compute a list of dates containg the start date and
# "steps" dates into the future, for a total of steps
# dates.
def get_dates_from_start(startDate, steps):
    dates = all_dates[all_dates.index(startDate):all_dates.index(startDate) + steps]
    return dates

# Get the next date of a given date
def get_next_date(startDate):
    return get_dates_from_start(startDate, 2)[1]

# Get a list of all the deaths by date for a given county,
# starting from the date of the first case
def get_deaths_list(FIPS, endDate=convert_date_to_yyyy_mm_dd(today)):
    # Extract only the rows for this county in order by date
    rows = daily_deaths.loc[daily_deaths["fips"] == FIPS]
    deaths_list = rows["deaths"].values
    dates_list = rows["date"].values
    
    if endDate in dates_list:
        index = list(dates_list).index(endDate)
    else:
        return []
    
    return deaths_list[0:index+1]

Today: 5/9/20
One week ago: 5/2/20


SVR Model Hyperparameters

In [52]:
kernel = 'rbf'
C = 100
gamma = 0.1
epsilon = 0.1

More Hyperparameters

In [53]:
specific_window = 1
window_limit = 14
s = 14
standard_error = 0.75

SVR Specific Functions

In [54]:
# For a county, trains up to a date, predicts s more days until the input date, and gets the losses.
def validation_loss(fips, s, window, test_end):
    data = get_deaths_list(fips, test_end)
    X, y = get_xy(data, window)
    newX = [x.astype("int") for x in X]
    X = np.array(newX)
    y = np.array(y)
    
    svr_rbf = SVR(kernel=kernel, C=C, gamma=gamma, epsilon=epsilon)
    model = svr_rbf.fit(X[:len(X)-s], y[:len(y)-s])
    
    train = data[:len(data)-s]
    last = train[len(train)-window:]
    loss = 0
    all_pred = []
    for i in range(s):
        pred = model.predict([last])
        all_pred.append(pred[0])
        true = y[len(y)-s+i]
        loss += (pred[0] - true)**2
        newlast = np.append(last[1:],pred)
        last = newlast
    return math.sqrt(loss/s), pinball_loss(y[len(y)-s:], all_pred)

# For a county, returns the best window size in range [a,b).
def best_window(fips, a, b, s, day):
    best = a
    try:
        rmse, pinball = validation_loss(fips, s, best, day)
    except:
        print("failed at 1")
        return best
    for w in range(a+1,b):
        try:
            new_rmse, new_pinball = validation_loss(fips, s, w, day)
            if new_pinball < pinball:
                pinball = new_pinball
                best = w
        except:
            print("failed at", w)
            break
    return best

In [55]:
# Prepares an array into sliding windows X and y.
def get_xy(arr, window):
    X, y = [], []
    for i in range(len(arr)-window):
        X.append(arr[i:i+window])
        y.append(arr[i+window])
    return X, y

# For a county, trains up to a date and predicts some days ahead of it. Doesn't get losses.
def forecast(fips, window, date, days):
    daily = get_deaths_list(fips, date)
    X, y = get_xy(daily, window)
    newX = [x.astype("int") for x in X]
    X = np.array(newX)
    y = np.array(y)
    
    svr_rbf = SVR(kernel=kernel, C=C, gamma=gamma, epsilon=epsilon)
    model = svr_rbf.fit(X, y)
    
    last = daily[len(daily)-window:]
    all_pred = []
    for i in range(days):
        pred = model.predict([last])
        all_pred.append(pred[0])
        newlast = np.append(last[1:],pred)
        last = newlast
    return all_pred

Right now we are training up to 5/5, as if that is all that we know. While training for each county, we choose a window size that minimizes a validation loss over the last week or two. Then, we predict 5/6 + 14 days.

In [56]:
key = pd.read_csv("../data/us/processing_data/fips_key.csv", encoding='latin-1')
all_fips = key["FIPS"].tolist()

n_steps = 18
start_date = '2020-05-09'
dates_of_interest = get_dates_from_start(get_next_date(start_date), n_steps)

data = {}
for fips in all_fips:
    data[fips] = {}
    window = best_window(fips, 1, window_limit, s, start_date)
    print(key.loc[key["FIPS"] == fips]["COUNTY"].values[0])
    print("Window:", window)
    
    try:
        pred = forecast(fips, window, start_date, n_steps)
        print("Pred:\n", pred)
        error = [x * standard_error for x in pred]
    except:
        pred, error = [0] * n_steps, [0] * n_steps
        print("Pred: failed")
    
    quantiles = generate_list_quantiles(pred, error)
    print("Quantiles:")
    for q in quantiles:
        print(q)
    print()
    
    for i, date in enumerate(dates_of_interest):
        data[fips][date] = quantiles[i]

Autauga County
Window: 13
Pred:
 [0.266487000128553, -0.03446406242685274, -0.048846267621151074, -0.021040334794197757, 0.5741577404742558, -0.10993509266470258, 0.07622886950059915, -0.12706626576829272, 0.3972753698477157, 0.6169661991308254, 0.7253044176378466, -0.01856826241786791, -0.07152369040203765, -0.19868586494642393, 0.18722484325839883, 0.19630666826368792, 0.3074580706823601, -0.059215926820299525]
Quantiles:
[0.010349375969529562, 0.09827616179404941, 0.16167756050547227, 0.21585171799911418, 0.266487000128553, 0.31712228225799177, 0.3712964397516336, 0.43469783846305654, 0.5226246242875764]
[nan, nan, nan, nan, nan, nan, nan, nan, nan]
[nan, nan, nan, nan, nan, nan, nan, nan, nan]
[nan, nan, nan, nan, nan, nan, nan, nan, nan]
[0.022298177093506122, 0.21174023112172058, 0.34834128036426326, 0.4650618402551441, 0.5741577404742558, 0.6832536406933676, 0.7999742005842483, 0.9365752498267912, 1.1260173038550056]
[nan, nan, nan, nan, nan, nan, nan, nan, nan]
[0.0029604492144

Blount County
Window: 1
Pred:
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Quantiles:
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]

Bullock County
Window: 1
Pred:
 [0.1, 

Pred:
 [0.17765927927912467, 0.2522004174999763, 0.19335177884512528, 0.1624196269878963, 0.22849585379289133, 0.30313058732580894, 0.29056967012607354, 0.24623976574615208, 0.2646074100765203, 0.3311205586893619, 0.36271878334103586, 0.3278468322899483, 0.3054247957479516, 0.3462780753346932, 0.408038291607083, 0.41100921974576304, 0.3645103650731853, 0.3589032772790956]
Quantiles:
[0.0068996336588589835, 0.06551791294219585, 0.10778581642313918, 0.14390218146620448, 0.17765927927912467, 0.21141637709204486, 0.24753274213511012, 0.2898006456160535, 0.34841892489939036]
[0.009794537591403973, 0.09300749763702579, 0.15300989631834916, 0.2042797336125326, 0.2522004174999763, 0.30012110138742, 0.3513909386816034, 0.4113933373629268, 0.4946062974085486]
[0.0075090726852725664, 0.07130505687626157, 0.11730644987557871, 0.15661294405270057, 0.19335177884512528, 0.23009061363754998, 0.2693971078146718, 0.315398500813989, 0.379194485004978]
[0.0063077815567648965, 0.059897771871391906, 0.09853

Quantiles:
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0

Colbert County
Window: 1
Pred:
 [0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1, 0.1]
Quantiles:
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.19611636741584504]
[0.0038836325841549585, 0.03687840748203143, 0.06066996154689693, 0.08099896726481502, 0.1, 0.11900103273518499, 0.13933003845310304, 0.1631215925179686, 0.1961163674

...

 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Quantiles:
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]

Waushara County
Window: 1
Pred:
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

Goshen County
Window: 1
Pred:
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Quantiles:
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]

Hot Springs County
Window: 1
Pred:
 [0

 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Quantiles:
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]

Natrona County
Window: 1
Pred:
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 

failed at 1
Aguadilla Municipio
Window: 1
Pred: failed
Quantiles:
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]

failed at 1
Aguas Buenas Municipio
Window: 1
Pred: failed
Quantiles:
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0,

[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]

failed at 1
Moca Municipio
Window: 1
Pred: failed
Quantiles:
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0, 0, 0, 0, 0]
[0, 0, 0, 0, 0

Output to submission file:

In [57]:
lists = []
for row_id in get_id_list():
    date = extract_date_from_id(row_id)
    fips = int(extract_fips_from_id(row_id))
    
    if not fips in data:
        lst = [row_id] + ["%.2f" % 0.00] * 9
        lists.append(lst)
        continue
        
    if not date in data[fips]:
        lst = [row_id] + ["%.2f" % 0.00] * 9
        lists.append(lst)
        continue
    
    quantiles = data[fips][date]
    lst = [row_id]
    for q in quantiles:
        if str(q) == "nan":
            lst.append("%.2f" % 0.00)
        elif q < 0:
            lst.append("%.2f" % 0.00)
        else:
            lst.append("%.2f" % q)
            
    lists.append(lst)
    
df = pd.DataFrame(lists, columns=sample_submission.columns)

df.to_csv("end_train_5-9_svm.csv", index=False, sep=',')